<a href="https://colab.research.google.com/github/phgandhi02/ISE789-Project/blob/main/Image_generation.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Text-guided image-to-image generation

The [StableDiffusionImg2ImgPipeline](https://huggingface.co/docs/diffusers/main/en/api/pipelines/stable_diffusion/img2img#diffusers.StableDiffusionImg2ImgPipeline) lets you pass a text prompt and an initial image to condition the generation of new images.

Before you begin, make sure you have all the necessary libraries installed:

In [ ]:
# uncomment to install the necessary libraries in Colab
!pip install diffusers transformers ftfy accelerate

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.0/2.0 MB 7.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 54.4/54.4 kB 2.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 297.4/297.4 kB 15.2 MB/s eta 0:00:00
  Using cached nvidia_cuda_nvrtc_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (23.7 MB)
  Using cached nvidia_cuda_runtime_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (823 kB)
  Using cached nvidia_cuda_cupti_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (14.1 MB)
  Using cached nvidia_cudnn_cu12-8.9.2.26-py3-none-manylinux1_x86_64.whl (731.7 MB)
  Using cached nvidia_cublas_cu12-12.1.3.1-py3-none-manylinux1_x86_64.whl (410.6 MB)
  Using cached nvidia_cufft_cu12-11.0.2.54-py3-none-manylinux1_x86_64.whl (121.6 MB)
  Using cached nvidia_curand_cu12-10.3.2.106-py3-none-manylinux1_x86_64.whl (56.5 MB)
  Using cached nvidia_cusolver_cu12-11.4.5.107-py3-none-manylinux1_x86_64.whl (124.2 MB)
  Using cached nvidia_cusparse_cu12-12.1.0.106-py3-none-manylinux

Get started by creating a [StableDiffusionImg2ImgPipeline](https://huggingface.co/docs/diffusers/main/en/api/pipelines/stable_diffusion/img2img#diffusers.StableDiffusionImg2ImgPipeline) with a pretrained Stable Diffusion model like [`nitrosocke/Ghibli-Diffusion`](https://huggingface.co/nitrosocke/Ghibli-Diffusion).

In [ ]:
import torch
import requests
from PIL import Image
from io import BytesIO
from diffusers import StableDiffusionImg2ImgPipeline
#"CompVis/stable-diffusion-v1-4"
device = "cuda"
model_path = "SG161222/Realistic_Vision_V6.0_B1_noVAE"

pipe = StableDiffusionImg2ImgPipeline.from_pretrained(model_path, torch_dtype=torch.float16).to(device)

The cache for model files in Transformers v4.22.0 has been updated. Migrating your old cache. This is a one-time only operation. You can interrupt this and resume the migration later on by calling `transformers.utils.move_cache()`.


0it [00:00, ?it/s]

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:88: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


model_index.json:   0%|          | 0.00/624 [00:00<?, ?B/s]

text_encoder/model.safetensors not found


...

vae/config.json:   0%|          | 0.00/601 [00:00<?, ?B/s]

diffusion_pytorch_model.bin:   0%|          | 0.00/3.44G [00:00<?, ?B/s]

diffusion_pytorch_model.bin:   0%|          | 0.00/335M [00:00<?, ?B/s]

Loading pipeline components...:   0%|          | 0/7 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/transformers/models/clip/feature_extraction_clip.py:28: FutureWarning: The class CLIPFeatureExtractor is deprecated and will be removed in version 5 of Transformers. Please use CLIPImageProcessor instead.
  warnings.warn(


Download and preprocess an initial image so you can pass it to the pipeline:

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

#url = "https://raw.githubusercontent.com/CompVis/stable-diffusion/main/assets/stable-samples/img2img/sketch-mountains-input.jpg"

#response = requests.get(url)
#init_image = Image.open(BytesIO(response.content)).convert("RGB")
#init_image.thumbnail((768, 768))
#init_image

Mounted at /content/drive


In [ ]:
import os

# Path to the mounted Google Drive directory
drive_path = '/content/drive/My Drive/'

# List the contents of the ISE789_images directory
images_dir = os.path.join(drive_path, 'ISE789_images')
image_files = os.listdir(images_dir)

# Get the first image file in the directory
if image_files:
    image_name = image_files[200]

    image_file_path = os.path.join(images_dir, image_name)
    print("Image Path:", image_file_path)
else:
    print("No image files found in the directory.")

# Check if the file exists
if os.path.isfile(image_file_path):
    # Load the image file as an image object
    image_obj = Image.open(image_file_path)
    # Display the image (optional)
    image_obj.show()
else:
    print("Image file not found.")

Image Path: /content/drive/My Drive/ISE789_images/000400.jpg


In [ ]:
from PIL import Image
import os

# Path to the mounted Google Drive directory
drive_path = '/content/drive/My Drive/'

# Path to the directory containing image files
images_dir = os.path.join(drive_path, 'ISE789_images')

# Path to the new directory where you want to save the images
new_images_dir = os.path.join(drive_path, 'New_Images')

# Create the new directory if it doesn't exist
os.makedirs(new_images_dir, exist_ok=True)

# Check if the images directory exists
if os.path.isdir(images_dir):
    # List all files in the directory
    image_files = os.listdir(images_dir)

    # Loop through each file in the directory
    for file_name in image_files[1:600]:
        # Check if the file is an image (you can add more image extensions as needed)
        if file_name.lower().endswith(('.png', '.jpg', '.jpeg', '.gif')):
            # Get the full path of the image file
            image_path = os.path.join(images_dir, file_name)

            # Open the image file as an image object
            image_obj = Image.open(image_path)
            prompt = ""
            neg_prompt = "((((nude, naked, nsfw)))"
            generator = torch.Generator(device=device).manual_seed(1024)
            image = pipe(prompt=prompt, negative_prompt=neg_prompt, image=image_obj, strength=0.2, guidance_scale=2.5, generator=generator).images[0]
            # Save the image to the new directory with the same filename
            new_image_path = os.path.join(new_images_dir, file_name)
            image.save(new_image_path)

            print(f"Image saved to: {new_image_path}")

        else:
            print(f"Skipping non-image file: {file_name}")
else:
    print("Images directory not found.")


  0%|          | 0/10 [00:00<?, ?it/s]

Image saved to: /content/drive/My Drive/New_Images/000589.jpg


  0%|          | 0/10 [00:00<?, ?it/s]

Image saved to: /content/drive/My Drive/New_Images/000567.jpg


  0%|          | 0/10 [00:00<?, ?it/s]

...

  0%|          | 0/10 [00:00<?, ?it/s]

Potential NSFW content was detected in one or more images. A black image will be returned instead. Try again with a different prompt and/or seed.


Image saved to: /content/drive/My Drive/New_Images/000049.jpg


  0%|          | 0/10 [00:00<?, ?it/s]

FileNotFoundError: [Errno 2] No such file or directory: '/content/drive/My Drive/New_Images/000044.jpg'

In [ ]:
prompt = ""
generator = torch.Generator(device=device).manual_seed(2024)
image = pipe(prompt=prompt, image=image_obj, strength=0.50, guidance_scale=2.5, generator=generator).images[0]
image